# KDD 2009 - Tratamento de dados simplificado

Este notebook foi criado para servir de exemplo de implementação de um modelo preditivo. O modelo mostra parte da solução do [KDD Cup de 2009](https://www.kdd.org/kdd-cup/view/kdd-cup-2009/Tasks).

### Descrição da tarefa do KDD 2009
A tarefa consiste em estimar as probabilidades de churn, appetency e up-selling de clisntes, já que estes são os tres objetivos a prever. Há duas variações do desafio, uma maior com 15.000 variáveis e outra, menor, com 230 variáveis.

Definições:
- ***Churn***: A taxa de *churn*, também chamada de taxa de atrito, é um dos dois fatores primários que determinam a estabilidade de um cliente que o negócio irá suportar. Em um sentido mais amplo, a taxa de *churn* é a medida do número de indivíduos ou itens que se movem para e de uma coleção em um período específico de tempo. O termo é utilizado em vários contextos, mas é aplicado de forma mais ampla em negócios no que tange a base contratual de clientes.
- ***Appetency***: No nosso contexto, *appetency*, é a propensão para comprar um serviço ou produto.
- ***Up-selling***: *Up-selling* é um técnica de venda onde um vendedor faz com que um consumidor compre itens mais caros, com upgrades, ou produtos adicionais em uma tentativa de aumentar o lucro das vendas. *Up-selling* normalmente indica vender produtos adicionais, que devem ser mais lucrativos que a venda original.


### Abordagem
Para resolver o problema baseado nos dados mais simples (230 variáveis do [KDD 2009](https://www.kdd.org/kdd-cup/view/kdd-cup-2009/Tasks)) seguiremos o seguinte roteiro geral:

1. Ler os dados do KDD 2009
2. Tratar os dados de forma simples, para extrair variáveis vazias ou com todos os valores nulos, que não tem impacto no modelo preditivo
3. Preparar os dados para utilizar o modelo preditivo escolhido (ver item 5)
4. Separar os dados em tres grupos:
    - Treinamento
    - Testes (ou validação)
    - Validação cruzada
5. Treinar o modelo com [XGBoost](https://xgboost.readthedocs.io/en/latest/index.html), escolhendo o número de rodadas de execução que produza o melhor resultado no grupo de testes. A métrica utilizada para avalizar o modelo, como descrito no desafio, será [AUC](https://en.wikipedia.org/wiki/AUC)
6. Validar este resultado com o grupo de validação cruzada. O resultado final será o mínimo entre os dois resultados
7. Como exercício adicional, vamos comparar a curva de resultados entre Testes (Validação) e Validação Cruzada, para avalizar, de forma superficial, como o modelo se comporta e verificar se há tendência de *overfitting* ou *underfitting*

In [1]:
# Importação de bibliotecas
import math
import numpy as np
import os
import pandas as pd
import random
from sklearn.metrics import auc
import sys
import xgboost as xgb

# Rotinas de visualização de dados
from bokeh.plotting import figure
from bokeh.io import output_notebook, push_notebook, show, export_png
from bokeh.models import Range1d

output_notebook()

Loading BokehJS ...

# Lendo arquivo de treinamento

O arquivo com dados de treinamento possui 50000 entradas. Os arquivos com os rótulos (churn, appetency, upselling) estão em separado e serão lidos mais tarde.

Os arquivos estão em formato TSV (valores separados por tab, com valores "não disponíveis" em branco

Por exemplo (os espaços são apenas ilustrativos)
```
Var1	Var2	Var3	Var4	Var5	Var6	Var7	Var8	Var9	Var10
\t      \t      \t      \t      1024\t    \t      \t    2048\t  \t      \t
```

Para ler estes dados usamos a função do pandas [`read_csv`](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.read_csv.html) indicando que o delimitador entre campos é o caracter tab (*\t*) e que os valores em branco/nulos são vazios.

Os valores são carregados no [dataframe](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.html) `kdd2009`.

In [2]:
# Diretório de dados
data_folder = os.path.join("..", "data")
# Arquivo de dados
training_data_file = os.path.join(data_folder, "orange_small_train.data")

# Dataframe com os dados de treinamento
kdd2009 = pd.read_csv(training_data_file, delimiter='\t', na_values=[''])

## Limpeza dos dados
Uma vez lidos os dados, é necessário verificar se há colunas apenas com NaNs (not a number) e remover estas colunas, caso existam. 

Para auxiliar o processo, criamos um dataframe com a contagem de NaNs (Not a Number) de cada coluna dos dados da Orange e depois criamos a lista das colunas que só possuem NaNs \([Not a Number](https://docs.python.org/3/library/math.html?highlight=nan#math.nan)\), mais tarde essas colunas serão removidas do dataframe de dados da Orange.

In [3]:
# Número total de pontos de dados
numeroDados = len(kdd2009)

# Cria dataframe com contagem de NaNs
nans = pd.DataFrame(kdd2009.isna().sum(), columns=['NAN_count'])

Examinando os 10 primeiros resultados... (por ordem de nome "***feature***")

In [4]:
nans.head(10)

NAN_count
Var1       49298
Var2       48759
Var3       48760
Var4       48421
Var5       48513
Var6        5529
Var7        5539
Var8       50000
Var9       49298
Var10      48513

Examinando os 20 "***features***" com maior ocorrência de *NaNs*

In [10]:
nans.sort_values(by=['NAN_count'], ascending=False).head(20)

NAN_count
Var230      50000
Var175      50000
Var55       50000
Var32       50000
Var141      50000
Var20       50000
Var39       50000
Var42       50000
Var167      50000
Var79       50000
Var31       50000
Var169      50000
Var15       50000
Var185      50000
Var8        50000
Var48       50000
Var209      50000
Var52       50000
Var92       49829
Var118      49829

In [5]:
# Recupera lista de variaveis que só possuem NaN
variaveisNulas = nans[nans['NAN_count'] == numeroDados].index.values

# Remove as colunas que só contém NaNs
kdd2009.drop(variaveisNulas, axis=1, inplace=True)

# Lendo arquivos de labels
Uma vez lidos os dados, é necessário ler os arquivos com os rótulos de cada um dos atributos que desejamos prever:
- *Appetency*: Propensão de contratar serviços
- *Churn*: Tendência de cancelar o contrato, também chamada de taxa de atrito)
- *Upselling*: Propensão de contratar serviços mais caros

Os rótulos estão em arquivos separados. Colunas com os tres rótulos serão incluídas no dataframe do kdd2009. Os arquivos de rótulos estão codificados em colunas, com -1 para falso e 1 para verdadeiro. Como no exemplo abaixo
```
-1
1
-1
-1
-1
-1
-1
-1
-1
-1

```

In [6]:
# Lendo arquivos com os rótulos das métricas
# Colunas de resultados
resultados = ['appetency', 'churn', 'upselling']
padraoArquivosRotulos = "orange_small_train_{}.labels"

# Colunas de variáveis de entrada
variaveis = kdd2009.keys()

# Le os arquivos de rótulos, converte 1 -> True, -1 -> False e inclui no dataframe do kdd
for rotulo in resultados:
    # Gera nome do arquivo
    nomeArquivo = os.path.join(data_folder, padraoArquivosRotulos.format(rotulo))
    # Lê arquivo
    dfRotulo = pd.read_csv(nomeArquivo, header=None, names=['label'])
    # Converte 1 -> True, -1 -> False - Assume que != 1 -> False
    dfRotulo['label'] = dfRotulo['label'] == 1
    # Inclusão dos rótulos no dataframe do kdd como colunas adicionais
    kdd2009[rotulo] = dfRotulo['label']

# Verificando os rótulos no DataFrame
Rápida visualização dos dados dos rótulos

In [11]:
# Primeiros valores dos resultados no dataframe de treinamento
kdd2009[resultados].head(10)

appetency  churn  upselling
0      False  False      False
1      False   True      False
2      False  False      False
3      False  False      False
4      False  False      False
5      False  False      False
6      False  False      False
7      False  False      False
8      False  False      False
9      False  False      False

## E verificando as variáveis (já sem colunas de NaNs)

In [12]:
# Primeiros valores das variaveis no dataframe de treinamento
kdd2009[variaveis].head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1526.0   7.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   525.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN  5236.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN     NaN   0.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN  1029.0   7.0   NaN    NaN    NaN  ...   

    Var220   Var221   Var222      Var223  Var224  Var225  Var226   Var227  \
0  1YVfGrO     oslk  fXVEsaq  jySVZNlOJy     NaN     NaN    xb3V     RAYp   
1  0AJo2f2     oslk  2Kb5FSF  LM8l689qOp     NaN     NaN    fKCe     RAYp   
2  JFM1BiF  Al6ZaUT  NKv4yOc  jySVZNlOJy     NaN    kG3k    Qu4f  02N6s8f   
3  L91KIiz     oslk  CE7uk3u  LM8l689qOp     NaN     NaN    FSa2     RAYp   
4  OrnLfvc     oslk  1J2cvxe  LM8l689qOp     NaN    kG3k    FSa2     RAYp   

          Var228  Var229  
0  F2FyR07IdsN7I     NaN  
1  F2FyR07IdsN7I     NaN  
2  ib5G6X1eUxUn6    am7c  
3  F2FyR07IdsN7I     NaN  
4  F2FyR07IdsN7I    mj86  

[5 rows x 212 columns]

## Verificando a correlação entre colunas
Utilizando coeficiente de correlação de [Pearson](https://en.wikipedia.org/wiki/Pearson_correlation_coefficient)

In [13]:
correlacao = kdd2009[variaveis].corr(method='pearson')
correlacao.head()

Var1      Var2      Var3  Var4  Var5  Var6  Var7      Var9     Var10  \
Var1   1.0       NaN       NaN   NaN   NaN   NaN   NaN  0.900828       NaN   
Var2   NaN  1.000000 -0.002711   NaN   NaN   NaN   NaN       NaN       NaN   
Var3   NaN -0.002711  1.000000   NaN   NaN   NaN   NaN       NaN       NaN   
Var4   NaN       NaN       NaN   1.0   NaN   NaN   NaN       NaN       NaN   
Var5   NaN       NaN       NaN   NaN   1.0   NaN   NaN       NaN  0.161563   

         Var11  ...    Var180  Var181   Var182    Var183    Var184    Var186  \
Var1       NaN  ...  0.210084     NaN      NaN       NaN       NaN  0.000525   
Var2 -0.006198  ...       NaN     NaN      NaN  0.030137  0.050524       NaN   
Var3  0.003885  ...       NaN     NaN      NaN  0.081396  0.021622       NaN   
Var4       NaN  ...       NaN     NaN  0.03495       NaN       NaN       NaN   
Var5       NaN  ...       NaN     NaN      NaN       NaN       NaN       NaN   

        Var187    Var188    Var189    Var190  
Var1  0.880618       NaN -0.068517       NaN  
Var2       NaN  0.018761 -0.068326       NaN  
Var3       NaN  0.093520  0.009123       NaN  
Var4       NaN       NaN  0.026948       NaN  
Var5       NaN       NaN -0.071298  0.137581  

[5 rows x 174 columns]

## Lista variáveis com maior índice de correlação
Para cada uma das variáveis, lista as que possuem o mais alto índice de correlação

In [14]:
limite = 0.99

In [15]:
for variavel in correlacao.index:
    correlacoes = correlacao[correlacao[variavel].abs() > limite]
    if len(correlacoes) > 1:
        print('---> Coluna: {}'.format(variavel))
        for coluna in correlacoes.index:
            if coluna != variavel:
                print('{}: {}'.format(coluna, correlacoes[variavel][coluna]))
        print()

---> Coluna: Var9
Var66: 0.9999996441554745
Var156: 0.9999996441554707

---> Coluna: Var21
Var22: 0.9999999999998949

---> Coluna: Var22
Var21: 0.9999999999998949

---> Coluna: Var66
Var9: 0.9999996441554745
Var156: 1.0000000000000075

---> Coluna: Var71
Var91: 0.9999999999999943
Var148: 0.9999999999999943

---> Coluna: Var88
Var128: 0.9999999999999976
Var145: 1.0000000000000038

---> Coluna: Var91
Var71: 0.9999999999999943
Var148: 1.0

---> Coluna: Var104
Var105: 0.9999999999999978

---> Coluna: Var105
Var104: 0.9999999999999978

---> Coluna: Var128
Var88: 0.9999999999999976
Var145: 1.000000000000007

---> Coluna: Var145
Var88: 1.0000000000000038
Var128: 1.000000000000007

---> Coluna: Var148
Var71: 0.9999999999999943
Var91: 1.0

---> Coluna: Var156
Var9: 0.9999996441554707
Var66: 1.0000000000000075



# Conversão de colunas de objetos e booleanos para inteiros

### Modelo baseado no XGBoost
Para utilizar o [XGBoost](https://xgboost.readthedocs.io/en/latest/index.html) é necessário converter as colunas de objetos e valores booleanos para inteiros ou reais.

Inicialmente vamos classificar as colunas em inteiros, reais, objetos e booleanos e depois converter objetos e booleanos para inteiros, já que o algoritmo que será utilizado para treinamento do modelo requer que os dados sejam inteiros ou reais.

In [16]:
# Verifica os tipos de dados existentes no dataframe
print('Lista de tipos de dados no kdd2009: {}'.format(list(set(kdd2009[variaveis].dtypes))))

Lista de tipos de dados no kdd2009: [dtype('O'), dtype('float64'), dtype('int64')]


In [17]:
data_types = pd.DataFrame(kdd2009[variaveis].dtypes, columns=['dtype'])

variaveisInteiras = list(data_types[data_types.values == np.dtype('int64')].index.values)
variaveisReais = list(data_types[data_types.values == np.dtype('float64')].index.values)
variaveisCategoricas = list(data_types[data_types.values == np.dtype('object')].index.values)

len(variaveisInteiras+variaveisReais+variaveisCategoricas+resultados) == len(kdd2009.keys())

print('Há {} variáveis inteiras, {} variáveis reais e {} objetos'.format(
                                                                    len(variaveisInteiras),
                                                                    len(variaveisReais),
                                                                    len(variaveisCategoricas)))

# Verifica se o total de tipos de variáveis está correto
if len(variaveisInteiras+variaveisReais+variaveisCategoricas+resultados) != len(kdd2009.keys()):
    print('Aviso: erro na contagem de tipos de variáveis!!!')

Há 1 variáveis inteiras, 173 variáveis reais e 38 objetos


## Breve verificação dos dados de cada tipo

In [18]:
kdd2009[variaveisCategoricas].head()

Var191      Var192   Var193 Var194 Var195 Var196 Var197   Var198  \
0    NaN  bZkvyxLkBI     RO12    NaN   taul   1K8T   lK27  ka_ns41   
1    NaN  CEat0G8rTN     RO12    NaN   taul   1K8T   2Ix5  qEdASpP   
2    NaN  eOQt0GoOh3  AERks4l   SEuy   taul   1K8T   ffXs  NldASpP   
3    NaN  jg69tYsGvO     RO12    NaN   taul   1K8T   ssAy  _ybO0dd   
4    NaN  IXSgUHShse     RO12   SEuy   taul   1K8T   uNkU  EKR938I   

          Var199   Var200  ...   Var220   Var221   Var222      Var223 Var224  \
0     nQUveAzAF7      NaN  ...  1YVfGrO     oslk  fXVEsaq  jySVZNlOJy    NaN   
1     y2LIM01bE1      NaN  ...  0AJo2f2     oslk  2Kb5FSF  LM8l689qOp    NaN   
2        y4g9XoZ  vynJTq9  ...  JFM1BiF  Al6ZaUT  NKv4yOc  jySVZNlOJy    NaN   
3  4hMlgkf58mhwh      NaN  ...  L91KIiz     oslk  CE7uk3u  LM8l689qOp    NaN   
4        ThrHXVS  0v21jmy  ...  OrnLfvc     oslk  1J2cvxe  LM8l689qOp    NaN   

  Var225 Var226   Var227         Var228 Var229  
0    NaN   xb3V     RAYp  F2FyR07IdsN7I    NaN  
1    NaN   fKCe     RAYp  F2FyR07IdsN7I    NaN  
2   kG3k   Qu4f  02N6s8f  ib5G6X1eUxUn6   am7c  
3    NaN   FSa2     RAYp  F2FyR07IdsN7I    NaN  
4   kG3k   FSa2     RAYp  F2FyR07IdsN7I   mj86  

[5 rows x 38 columns]

## Cálculos de estatísticas descritivas básicas das colunas de dados

In [19]:
kdd2009.describe()

Var1         Var2           Var3         Var4          Var5  \
count  702.000000  1241.000000    1240.000000  1579.000000  1.487000e+03   
mean    11.487179     0.004029     425.298387     0.125396  2.387933e+05   
std     40.709951     0.141933    4270.193518     1.275481  6.441259e+05   
min      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
25%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
50%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
75%     16.000000     0.000000       0.000000     0.000000  1.187425e+05   
max    680.000000     5.000000  130668.000000    27.000000  6.048550e+06   

                Var6          Var7         Var9         Var10        Var11  \
count   44471.000000  44461.000000   702.000000  1.487000e+03  1240.000000   
mean     1326.437116      6.809496    48.145299  3.926057e+05     8.625806   
std      2685.693668      6.326053   154.777855  9.280896e+05     2.869558   
min         0.000000      0.000000     0.000000  0.000000e+00     8.000000   
25%       518.000000      0.000000     4.000000  0.000000e+00     8.000000   
50%       861.000000      7.000000    20.000000  0.000000e+00     8.000000   
75%      1428.000000      7.000000    46.000000  2.628630e+05     8.000000   
max    131761.000000    140.000000  2300.000000  1.232559e+07    40.000000   

       ...        Var180        Var181        Var182        Var183  \
count  ...  7.020000e+02  44991.000000  1.579000e+03  1.241000e+03   
mean   ...  3.776755e+06      0.611456  1.416638e+06  7.777380e+04   
std    ...  3.785696e+06      2.495681  2.279786e+06  2.016188e+05   
min    ...  0.000000e+00      0.000000  0.000000e+00  0.000000e+00   
25%    ...  1.917352e+05      0.000000  0.000000e+00  0.000000e+00   
50%    ...  2.431310e+06      0.000000  1.167780e+05  0.000000e+00   
75%    ...  6.471827e+06      0.000000  1.844952e+06  4.881000e+04   
max    ...  1.428483e+07     49.000000  1.199478e+07  3.048400e+06   

            Var184      Var186     Var187       Var188        Var189  \
count  1241.000000  702.000000  702.00000  1241.000000  21022.000000   
mean      8.460919    3.299145   16.54416   167.368477    270.142137   
std      46.973777    8.781967   60.22303   113.980072     86.707692   
min       0.000000    0.000000    0.00000    -6.420000      6.000000   
25%       0.000000    0.000000    0.00000    19.380000    204.000000   
50%       0.000000    0.000000    4.00000   197.640000    270.000000   
75%       8.000000    6.000000   14.00000   252.960000    330.000000   
max    1200.000000  102.000000  910.00000   628.620000    642.000000   

              Var190  
count     333.000000  
mean    22007.045192  
std     29085.146490  
min         0.000000  
25%      2732.670000  
50%     12668.940000  
75%     29396.340000  
max    230427.000000  

[8 rows x 174 columns]

In [20]:
kdd2009.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1526.0   7.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   525.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN  5236.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN     NaN   0.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN  1029.0   7.0   NaN    NaN    NaN  ...   

       Var223  Var224  Var225  Var226   Var227         Var228  Var229  \
0  jySVZNlOJy     NaN     NaN    xb3V     RAYp  F2FyR07IdsN7I     NaN   
1  LM8l689qOp     NaN     NaN    fKCe     RAYp  F2FyR07IdsN7I     NaN   
2  jySVZNlOJy     NaN    kG3k    Qu4f  02N6s8f  ib5G6X1eUxUn6    am7c   
3  LM8l689qOp     NaN     NaN    FSa2     RAYp  F2FyR07IdsN7I     NaN   
4  LM8l689qOp     NaN    kG3k    FSa2     RAYp  F2FyR07IdsN7I    mj86   

   appetency  churn  upselling  
0      False  False      False  
1      False   True      False  
2      False  False      False  
3      False  False      False  
4      False  False      False  

[5 rows x 215 columns]

## Convertendo variáveis categóricas para inteiros (para usar no XGBoost)

In [21]:
# Cada variável categórica é convertida para Categorical do Pandas e depois
# mudamos seu valor categórico para o código numérico correspondente
for variavel in variaveisCategoricas:
    kdd2009[variavel] = pd.Categorical(kdd2009[variavel])
    kdd2009[variavel] = kdd2009[variavel].cat.codes

In [22]:
# Verifica os tipos de dados existentes no dataframe
print('Lista de tipos de dados no kdd2009: {}'.format(list(set(kdd2009[variaveis].dtypes))))

Lista de tipos de dados no kdd2009: [dtype('float64'), dtype('int8'), dtype('int64'), dtype('int16')]


In [23]:
kdd2009.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1526.0   7.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   525.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN  5236.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN     NaN   0.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN  1029.0   7.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0       3      -1      -1      22       2       8      -1      False  False   
1       0      -1      -1      14       2       8      -1      False   True   
2       3      -1       1      10       0      25       0      False  False   
3       0      -1      -1       7       2       8      -1      False  False   
4       0      -1       1       7       2       8       1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

In [24]:
kdd2009.describe()

Var1         Var2           Var3         Var4          Var5  \
count  702.000000  1241.000000    1240.000000  1579.000000  1.487000e+03   
mean    11.487179     0.004029     425.298387     0.125396  2.387933e+05   
std     40.709951     0.141933    4270.193518     1.275481  6.441259e+05   
min      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
25%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
50%      0.000000     0.000000       0.000000     0.000000  0.000000e+00   
75%     16.000000     0.000000       0.000000     0.000000  1.187425e+05   
max    680.000000     5.000000  130668.000000    27.000000  6.048550e+06   

                Var6          Var7         Var9         Var10        Var11  \
count   44471.000000  44461.000000   702.000000  1.487000e+03  1240.000000   
mean     1326.437116      6.809496    48.145299  3.926057e+05     8.625806   
std      2685.693668      6.326053   154.777855  9.280896e+05     2.869558   
min         0.000000      0.000000     0.000000  0.000000e+00     8.000000   
25%       518.000000      0.000000     4.000000  0.000000e+00     8.000000   
50%       861.000000      7.000000    20.000000  0.000000e+00     8.000000   
75%      1428.000000      7.000000    46.000000  2.628630e+05     8.000000   
max    131761.000000    140.000000  2300.000000  1.232559e+07    40.000000   

       ...       Var220        Var221        Var222        Var223  \
count  ...  50000.00000  50000.000000  50000.000000  50000.000000   
mean   ...   2003.12184      3.984080   2123.702060      0.302480   
std    ...   1248.04682      1.119166   1183.541455      1.070238   
min    ...      0.00000      0.000000      0.000000     -1.000000   
25%    ...    826.00000      4.000000   1066.000000      0.000000   
50%    ...   2014.00000      4.000000   2230.000000      0.000000   
75%    ...   3047.00000      4.000000   2984.250000      0.000000   
max    ...   4290.00000      6.000000   4290.000000      3.000000   

             Var224        Var225        Var226        Var227        Var228  \
count  50000.000000  50000.000000  50000.000000  50000.000000  50000.000000   
mean      -0.983600     -0.220100     10.115720      2.103060     10.233400   
std        0.127009      0.933506      5.798438      0.867994      6.488254   
min       -1.000000     -1.000000      0.000000      0.000000      0.000000   
25%       -1.000000     -1.000000      6.000000      2.000000      8.000000   
50%       -1.000000     -1.000000     10.000000      2.000000      8.000000   
75%       -1.000000      1.000000     14.000000      2.000000      8.000000   
max        0.000000      2.000000     22.000000      6.000000     29.000000   

             Var229  
count  50000.000000  
mean      -0.368800  
std        0.799074  
min       -1.000000  
25%       -1.000000  
50%       -1.000000  
75%        0.000000  
max        3.000000  

[8 rows x 212 columns]

# Divisão do conjunto de dados em treinamento, validação e verificação cruzada
Os dados originais serão divididos em tres conjuntos:

- Treinamento, com 90% dos dados (45.000 dados)
- Validação, com 5% dos dados (2.500 dados)
- Verificação cruzada, com 5% dos dados (2.500 dados)

In [25]:
# Fixa semente para reproduzir resultados
random.seed(42)

# Define treino como 90% dos dados de treino e
# validação como os 10% restantes, metade para testes e
# metade para validação cruzada
tamanhoTreino = math.floor(0.9 * numeroDados)

# Gera uma amostra aleatória com 90% dos índices
indicesTreino = random.sample(range(numeroDados), tamanhoTreino)
# Indices de Validação (testes) e Validação Cruzada
indicesValidacaoVC = list(set(range(numeroDados)) - set(indicesTreino))
metade = len(indicesValidacaoVC)//2

indicesValidacao = indicesValidacaoVC[:metade]
indicesVCruzada = indicesValidacaoVC[metade:]

# Divide os dados nos tres subgrupos
# dadosTreino serão usados para treinar o modelo
# dadosValidacao serão usados para testar o modelo
# dadosVCruzada serão usados para estimar a performance do modelo
dadosTreino = kdd2009.iloc[indicesTreino].reset_index(drop=True)
dadosValidacao = kdd2009.iloc[indicesValidacao].reset_index(drop=True)
dadosVCruzada = kdd2009.iloc[indicesVCruzada].reset_index(drop=True)

# Dimensões dos dados de treino e validação
print("Dados de treinamento: {}, Dados de validação: {}, Dados de validação cruzada: {}".format(len(dadosTreino),
                                                                len(dadosValidacao),
                                                                len(dadosVCruzada)))

Dados de treinamento: 45000, Dados de validação: 2500, Dados de validação cruzada: 2500


## Verificando os dataframes

In [26]:
dadosTreino.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN   392.0   0.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN  1911.0   0.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN   854.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN  2331.0   7.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN   119.0   0.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0      -1      -1      -1       8       2       8      -1      False  False   
1       0      -1      -1      14       2       8      -1      False  False   
2       0      -1       1      12       1       2       0       True  False   
3       0      -1       0      17       4       8       0      False  False   
4      -1      -1      -1       1       0       8      -1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

In [27]:
dadosValidacao.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN  1204.0   0.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN   805.0   7.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN   539.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN  1155.0  14.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN   693.0   7.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0       0      -1      -1      16       2       8      -1      False  False   
1       0      -1       0       9       2       8       0      False  False   
2       0      -1      -1      18       2       8      -1      False   True   
3       3      -1       1       4       2       2       0      False  False   
4       0      -1      -1       7       2       8      -1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

In [28]:
dadosVCruzada.head()

Var1  Var2  Var3  Var4  Var5    Var6  Var7  Var9  Var10  Var11  ...  \
0   NaN   NaN   NaN   NaN   NaN    63.0   0.0   NaN    NaN    NaN  ...   
1   NaN   NaN   NaN   NaN   NaN  1344.0   7.0   NaN    NaN    NaN  ...   
2   NaN   NaN   NaN   NaN   NaN   308.0   7.0   NaN    NaN    NaN  ...   
3   NaN   NaN   NaN   NaN   NaN   840.0   7.0   NaN    NaN    NaN  ...   
4   NaN   NaN   NaN   NaN   NaN   126.0   0.0   NaN    NaN    NaN  ...   

   Var223  Var224  Var225  Var226  Var227  Var228  Var229  appetency  churn  \
0       0      -1      -1      11       2       8      -1      False  False   
1       0      -1      -1       0       2       8       0      False  False   
2       0      -1       2       4       2       8       1      False  False   
3       0      -1      -1      12       2       8      -1      False  False   
4       0      -1      -1       6       2       8      -1      False  False   

   upselling  
0      False  
1      False  
2      False  
3      False  
4      False  

[5 rows x 215 columns]

## Verificando a distribuição dos rótulos entre treino, testes e validação cruzada

In [29]:
dadosTreino[resultados].sum()

appetency     805
churn        3341
upselling    3327
dtype: int64

In [30]:
dadosValidacao[resultados].sum()

appetency     37
churn        159
upselling    164
dtype: int64

In [31]:
dadosVCruzada[resultados].sum()

appetency     48
churn        172
upselling    191
dtype: int64

# XGBoost

Utilizaremos o [XGBoost](https://xgboost.readthedocs.io/en/latest/index.html) para treinamento dos dados do KDD2009 e predição de resultados no conjunto de testes.

De acordo com o a página de ajuda do XGBoost:
XGBoost é uma biblioteca otimizada de gradient boosting distribuído, projetada para ser altamente eficiente, flexível e portável. Implementa algoritmos de machine learning sob o framework de Gradient [Boosting](https://en.wikipedia.org/wiki/Boosting_(machine_learning)). O XGBoost provê uma árvore paralela de boosting (também conhecida como GBDT, GBM) que pode resolver vários problemas de ciência de dados de forma rápida e precisa. O mesmo código é executado em vários ambientes distribuídos (Hadoop, SCG, MPI) e pode resolver problemas com mais de bilhões de exemplos.


In [32]:
# Variável que será prevista
resultado = 'upselling'

### Rotinas de chamada do XGBoost
Para executar o XGBoost criamos duas rotinas:
- `gradeBoost`: Recebe dados de treinamento, de teste, o rótulo a ser testado e um iterador para a grade de treinamento, essa rotina "envelopa" a função `xgBoost`.
- `xgBoost`: Rotina que chama o XGBoost com os parâmetros desejados

A métrica utilizada para avaliar o modelo, de acordo com o desafio KDD2009 é o AUC:

**TODO**: Explicar AUC e ROC (que será incluído mais tarde)

In [33]:
def matrizTeste(teste, listaVariaveis):
    return xgb.DMatrix(teste[listaVariaveis])

def matrizTreino(treinamento, listaVariaveis):
    return xgb.DMatrix(treinamento[listaVariaveis], treinamento[[rotulo]])

def computaAUC(dados, listaVariaveis, rotulo, modelo):
    matriz = matrizTeste(dados, listaVariaveis)
    resultadoValidacao = modelo.predict(matriz)
    validacao = dados[rotulo].apply(int).reset_index(drop=True)
    previsao = 'previsao'
    dfPrevisao = pd.DataFrame(resultadoValidacao, columns=[previsao])
    dfPrevisao[resultado] = validacao
    dfPrevisao = dfPrevisao.sort_values(by=previsao)
    return auc(dfPrevisao[previsao], dfPrevisao[rotulo])

def gradeBoost(treinamento, listaVariaveis, teste, rotulo, intervaloGrade, verbose=0):
    """ Gera lista de resultados da grade de treinamento.
    Parâmetros:
    treinamento: Dataframe de dados de treinamento, com variaveis e rotulos
    listaVariaveis: Lista de variáveis para treinamento/teste
    teste: Dataframe de dados de teste/validação
    rotulo: Rotulo do teste
    intervaloGrade: Range de intervalo da grade de treinamento
    """
    # TODO: Tratamento de parâmetros/datarames de entrada
    
    # Converte dataframes para DMatrices
    xgbDados = matrizTreino(treinamento, listaVariaveis)
    xgbTeste = matrizTeste(teste, listaVariaveis)
    
    # Converte rotulos booleanos para inteiro (embora não seja estritamente necessário em python)
    validacao = teste[rotulo].apply(int).reset_index(drop=True)

    # Vetor de resultados
    resultados = []
    melhorAUC = float("-inf")
    melhorRodadas = -1
    dataFrame, modelo = (None, None)
    
    # Indices das tuplas
    rodadaXGB = 0
    aucRodada = -1
    for rodada in intervaloGrade:
        resultado = xgBoost(xgbDados, xgbTeste, validacao, rotulo, rodada, verbose=verbose)
        if resultado['resultado'][aucRodada] > melhorAUC:
            melhorAUC = resultado['resultado'][aucRodada]
            melhorRodadas = resultado['resultado'][rodadaXGB]
            dataFrame = resultado['df']
            modelo = resultado['modelo']
        resultados.append(resultado['resultado'])
            
    return {'melhor': {'auc': melhorAUC,
                       'rodadas': melhorRodadas,
                       'dataframe': dataFrame,
                       'modelo': modelo},
            'resultados': resultados}

def xgBoost(treinamento, teste, validacao, rotulo, rodadas, verbose=0):
    """ Executa o xgBoost e retorna tupla com número de rodadas e AUC
    """
    param = {'booster': 'dart',
             #'objective': 'binary:logistic',
             #'eta': 0.05,
             #'gamma': 0,
             'max_depth': 8,
             #'min_child_weight': 1,
             #'subsample': 1,
             #'colsample_bytree': 1
            }
    if verbose:
        print('XGBoost, {rodadas} rodadas'.format(rodadas=rodadas))
    # Treina modelo pelo número de rodadas determinado
    modelo = xgb.train(param, treinamento, rodadas)
    
    # Computa a previsão do modelo para o conjunto de teste
    resultadoValidacao = modelo.predict(teste)

    # Cria dataframe com previsão e rótulo
    previsao = 'previsao'
    dfPrevisao = pd.DataFrame(resultadoValidacao, columns=[previsao])
    dfPrevisao[rotulo] = validacao
    
    # Ordena o dataframe pela coluna de previsao
    dfPrevisao = dfPrevisao.sort_values(by=previsao)
    # Usamos o AUC do sklearn.metrics
    # requer: from sklearn.metrics import auc
    aucRun = auc(dfPrevisao[previsao], dfPrevisao[rotulo])
    if verbose:
        print('----------> AUC: {}'.format(aucRun))
    return {'df': dfPrevisao, 'modelo': modelo, 'resultado':(rodadas, aucRun)}
    

# Visualização de resultados
Rotinas bokeh para visualização de gráficos de linhas dos resultados

In [34]:
# Rotinas para geração de gráficos
def linha(dados, x="x", y="y", fig=None, delay=False, **kwargs):
    p = figure(width=900, height=600) if fig == None else fig
    p.y_range = Range1d(0,1)
    p.line(x, y, source=dados, **kwargs)
    if delay == False:
        show(p)
    return p
    
def linhaAUC(dados, fig=None, delay=False, **kwargs):
    return linha(dados, x="Rodadas", y="AUC", fig=fig, delay=delay, **kwargs)

In [35]:
# Iterador para a grade de busca
iteracoes = range(5, 150, 1)

In [36]:
grade = gradeBoost(dadosTreino, variaveis, dadosValidacao, resultado, iteracoes, verbose=1)

XGBoost, 5 rodadas
[18:54:48] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[18:54:48] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:54:48] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 268 extra nodes, 0 pruned nodes, max_depth=8
[18:54:48] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:54:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 258 extra nodes, 0 pruned nodes, max_depth=8
[18:54:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:54:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 272 extra nodes, 0 pruned nodes, max_depth=8
[18:54:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:54:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 288 extra nodes, 0 pruned nodes, max_depth=8
[18:54:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
---------->

[18:54:59] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 238 extra nodes, 0 pruned nodes, max_depth=8
[18:54:59] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:54:59] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 296 extra nodes, 0 pruned nodes, max_depth=8
[18:54:59] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:00] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 252 extra nodes, 0 pruned nodes, max_depth=8
[18:55:00] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:00] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 254 extra nodes, 0 pruned nodes, max_depth=8
[18:55:00] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
----------> AUC: 0.4674098491668701
XGBoost, 11 rodadas
[18:55:00] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[18:55:00] /workspace/src/gbm/gbtree.cc:492:

[18:55:11] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 272 extra nodes, 0 pruned nodes, max_depth=8
[18:55:11] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:11] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 288 extra nodes, 0 pruned nodes, max_depth=8
[18:55:11] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:11] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 256 extra nodes, 0 pruned nodes, max_depth=8
[18:55:11] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:11] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 238 extra nodes, 0 pruned nodes, max_depth=8
[18:55:11] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:11] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 296 extra nodes, 0 pruned nodes, max_depth=8
[18:55:11] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:12] /workspace/src/tree

----------> AUC: 0.4947349280118942
XGBoost, 17 rodadas
[18:55:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[18:55:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 268 extra nodes, 0 pruned nodes, max_depth=8
[18:55:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 258 extra nodes, 0 pruned nodes, max_depth=8
[18:55:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 272 extra nodes, 0 pruned nodes, max_depth=8
[18:55:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:23] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 288 extra nodes, 0 pruned nodes, max_depth=8
[18:55:23] /workspace/src/gbm/gbtree.cc:492:

[18:55:35] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 296 extra nodes, 0 pruned nodes, max_depth=8
[18:55:35] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:35] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 252 extra nodes, 0 pruned nodes, max_depth=8
[18:55:35] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:35] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 254 extra nodes, 0 pruned nodes, max_depth=8
[18:55:35] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:36] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 300 extra nodes, 0 pruned nodes, max_depth=8
[18:55:36] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:36] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 226 extra nodes, 0 pruned nodes, max_depth=8
[18:55:36] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[18:55:36] /workspace/src/tree

...

[10:17:51] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=8
[10:17:51] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:17:51] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 60 extra nodes, 0 pruned nodes, max_depth=8
[10:17:51] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:17:52] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 278 extra nodes, 0 pruned nodes, max_depth=8
[10:17:52] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:17:52] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 322 extra nodes, 0 pruned nodes, max_depth=8
[10:17:52] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:17:53] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 256 extra nodes, 0 pruned nodes, max_depth=8
[10:17:53] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:17:54] /workspace/src/tree/

[10:18:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 308 extra nodes, 0 pruned nodes, max_depth=8
[10:18:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
----------> AUC: 0.5745491236448288
XGBoost, 149 rodadas
[10:18:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[10:18:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 268 extra nodes, 0 pruned nodes, max_depth=8
[10:18:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 258 extra nodes, 0 pruned nodes, max_depth=8
[10:18:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:15] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 272 extra nodes, 0 pruned nodes, max_depth=8
[10:18:15] /workspace/src/gbm/gbtree.cc:492

[10:18:25] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 198 extra nodes, 0 pruned nodes, max_depth=8
[10:18:25] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:25] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 236 extra nodes, 0 pruned nodes, max_depth=8
[10:18:25] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:25] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 190 extra nodes, 0 pruned nodes, max_depth=8
[10:18:25] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:25] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 240 extra nodes, 0 pruned nodes, max_depth=8
[10:18:25] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:26] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 258 extra nodes, 0 pruned nodes, max_depth=8
[10:18:26] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:26] /workspace/src/tree

[10:18:38] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 226 extra nodes, 0 pruned nodes, max_depth=8
[10:18:38] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:38] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 298 extra nodes, 0 pruned nodes, max_depth=8
[10:18:38] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:38] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 284 extra nodes, 0 pruned nodes, max_depth=8
[10:18:38] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:39] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 206 extra nodes, 0 pruned nodes, max_depth=8
[10:18:39] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:39] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 288 extra nodes, 0 pruned nodes, max_depth=8
[10:18:39] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:39] /workspace/src/tree

[10:18:54] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 260 extra nodes, 0 pruned nodes, max_depth=8
[10:18:54] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:54] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 270 extra nodes, 0 pruned nodes, max_depth=8
[10:18:54] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:55] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=8
[10:18:55] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:55] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 298 extra nodes, 0 pruned nodes, max_depth=8
[10:18:55] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:56] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 240 extra nodes, 0 pruned nodes, max_depth=8
[10:18:56] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[10:18:56] /workspace/src/tree

In [37]:
grade['resultados']

[(5, 0.3566015511751175),
 (6, 0.3737172782421112),
 (7, 0.3657975047826767),
 (8, 0.3964189440011978),
 (9, 0.46365486085414886),
 (10, 0.4674098491668701),
 (11, 0.44351303577423096),
 (12, 0.4840465635061264),
 (13, 0.5002228170633316),
 (14, 0.48310407996177673),
 (15, 0.5024404227733612),
 (16, 0.4947349280118942),
 (17, 0.49558936059474945),
 (18, 0.49240198731422424),
 (19, 0.471107080578804),
 (20, 0.4878058135509491),
 (21, 0.4861430823802948),
 (22, 0.48552779853343964),
 (23, 0.49713170528411865),
 (24, 0.4971563220024109),
 (25, 0.4923430234193802),
 (26, 0.5115413814783096),
 (27, 0.5102210938930511),
 (28, 0.5034476220607758),
 (29, 0.5174935758113861),
 (30, 0.5148542821407318),
 (31, 0.5136159211397171),
 (32, 0.5189609825611115),
 (33, 0.5240499824285507),
 (34, 0.5173920094966888),
 (35, 0.5004170089960098),
 (36, 0.5058133751153946),
 (37, 0.502229630947113),
 (38, 0.49806733429431915),
 (39, 0.5002453625202179),
 (40, 0.5082923620939255),
 (41, 0.5135435163974762),


In [38]:
dfGrade = pd.DataFrame({"AUC":[g[1] for g in grade['resultados']], "Rodadas":[g[0] for g in grade['resultados']]})

In [39]:
aucMax = grade['melhor']['auc']
numRodadas = grade['melhor']['rodadas']
print('AUC Máximo: {}, {} rodadas'.format(aucMax, numRodadas))

AUC Máximo: 0.6576421707868576, 80 rodadas


In [40]:
fig = linhaAUC(dfGrade, color="red", legend="Teste")

## Resultado da Validação Cruzada
A medida AUC estimada é dada pelo mínimo entre a melhor performance dos dados de **Teste** e o resultado da **Validação Cruzada**

In [41]:
aucVC = computaAUC(dadosVCruzada, variaveis, rotulo, grade['melhor']['modelo'])
print('Performance estimada do modelo (AUC): {}'.format(min(aucMax, aucVC)))

Performance estimada do modelo (AUC): 0.5976349860429764


# Comparação de comportamento entre Testes e Validação Cruzada

Para ter uma ideia mais clara da previsibilidade do modelo, vamos comparar os resultados globais dos dados de Testes (e não apenas o melhor resultado) com os resultados com os dados de Validação Cruzada 

In [42]:
gradeVCruzada = gradeBoost(dadosTreino, variaveis, dadosVCruzada, resultado, iteracoes, verbose=1)

XGBoost, 5 rodadas
[13:37:20] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[13:37:20] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:37:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 268 extra nodes, 0 pruned nodes, max_depth=8
[13:37:21] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:37:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 258 extra nodes, 0 pruned nodes, max_depth=8
[13:37:21] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:37:21] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 272 extra nodes, 0 pruned nodes, max_depth=8
[13:37:21] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:37:22] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 288 extra nodes, 0 pruned nodes, max_depth=8
[13:37:22] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
---------->

[13:37:34] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 238 extra nodes, 0 pruned nodes, max_depth=8
[13:37:34] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:37:35] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 296 extra nodes, 0 pruned nodes, max_depth=8
[13:37:35] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:37:36] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 252 extra nodes, 0 pruned nodes, max_depth=8
[13:37:36] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:37:36] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 254 extra nodes, 0 pruned nodes, max_depth=8
[13:37:36] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
----------> AUC: 0.4520387351512909
XGBoost, 11 rodadas
[13:37:37] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[13:37:37] /workspace/src/gbm/gbtree.cc:492:

[13:38:02] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 258 extra nodes, 0 pruned nodes, max_depth=8
[13:38:02] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:03] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 272 extra nodes, 0 pruned nodes, max_depth=8
[13:38:03] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:03] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 288 extra nodes, 0 pruned nodes, max_depth=8
[13:38:03] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:03] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 256 extra nodes, 0 pruned nodes, max_depth=8
[13:38:03] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:04] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 238 extra nodes, 0 pruned nodes, max_depth=8
[13:38:04] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:04] /workspace/src/tree

[13:38:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 152 extra nodes, 0 pruned nodes, max_depth=8
[13:38:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
----------> AUC: 0.4791940450668335
XGBoost, 17 rodadas
[13:38:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[13:38:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 268 extra nodes, 0 pruned nodes, max_depth=8
[13:38:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:15] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 258 extra nodes, 0 pruned nodes, max_depth=8
[13:38:15] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:15] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 272 extra nodes, 0 pruned nodes, max_depth=8
[13:38:15] /workspace/src/gbm/gbtree.cc:492:

[13:38:26] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 238 extra nodes, 0 pruned nodes, max_depth=8
[13:38:26] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 296 extra nodes, 0 pruned nodes, max_depth=8
[13:38:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 252 extra nodes, 0 pruned nodes, max_depth=8
[13:38:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 254 extra nodes, 0 pruned nodes, max_depth=8
[13:38:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:27] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 300 extra nodes, 0 pruned nodes, max_depth=8
[13:38:27] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[13:38:28] /workspace/src/tree

...

[14:47:40] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 170 extra nodes, 0 pruned nodes, max_depth=8
[14:47:40] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:47:41] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 192 extra nodes, 0 pruned nodes, max_depth=8
[14:47:41] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:47:41] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 122 extra nodes, 0 pruned nodes, max_depth=8
[14:47:41] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:47:42] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 60 extra nodes, 0 pruned nodes, max_depth=8
[14:47:42] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:47:42] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 278 extra nodes, 0 pruned nodes, max_depth=8
[14:47:42] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:47:42] /workspace/src/tree/

[14:48:00] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 250 extra nodes, 0 pruned nodes, max_depth=8
[14:48:00] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:01] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 354 extra nodes, 0 pruned nodes, max_depth=8
[14:48:01] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:01] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 308 extra nodes, 0 pruned nodes, max_depth=8
[14:48:01] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
----------> AUC: 0.6481539607048035
XGBoost, 149 rodadas
[14:48:02] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 248 extra nodes, 0 pruned nodes, max_depth=8
[14:48:02] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:02] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 268 extra nodes, 0 pruned nodes, max_depth=8
[14:48:02] /workspace/src/gbm/gbtree.cc:492

[14:48:13] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 112 extra nodes, 0 pruned nodes, max_depth=8
[14:48:13] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:13] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 154 extra nodes, 0 pruned nodes, max_depth=8
[14:48:13] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:13] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 198 extra nodes, 0 pruned nodes, max_depth=8
[14:48:13] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:13] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 236 extra nodes, 0 pruned nodes, max_depth=8
[14:48:13] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:14] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 190 extra nodes, 0 pruned nodes, max_depth=8
[14:48:14] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:14] /workspace/src/tree

[14:48:29] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 246 extra nodes, 0 pruned nodes, max_depth=8
[14:48:29] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:29] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 240 extra nodes, 0 pruned nodes, max_depth=8
[14:48:29] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:30] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 226 extra nodes, 0 pruned nodes, max_depth=8
[14:48:30] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:30] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 298 extra nodes, 0 pruned nodes, max_depth=8
[14:48:30] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:31] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 284 extra nodes, 0 pruned nodes, max_depth=8
[14:48:31] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:31] /workspace/src/tree

[14:48:48] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 366 extra nodes, 0 pruned nodes, max_depth=8
[14:48:48] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 264 extra nodes, 0 pruned nodes, max_depth=8
[14:48:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:49] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 260 extra nodes, 0 pruned nodes, max_depth=8
[14:48:49] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:50] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 270 extra nodes, 0 pruned nodes, max_depth=8
[14:48:50] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:50] /workspace/src/tree/updater_prune.cc:74: tree pruning end, 1 roots, 188 extra nodes, 0 pruned nodes, max_depth=8
[14:48:50] /workspace/src/gbm/gbtree.cc:492: drop 0 trees, weight = 1
[14:48:50] /workspace/src/tree

In [43]:
gradeVCruzada['resultados']

[(5, 0.3908200263977051),
 (6, 0.41635143756866455),
 (7, 0.4245189428329468),
 (8, 0.4568527787923813),
 (9, 0.4580366760492325),
 (10, 0.4520387351512909),
 (11, 0.47967293858528137),
 (12, 0.4442639797925949),
 (13, 0.4733268916606903),
 (14, 0.47780337929725647),
 (15, 0.4739969074726105),
 (16, 0.4791940450668335),
 (17, 0.48501358926296234),
 (18, 0.4758099764585495),
 (19, 0.48632732033729553),
 (20, 0.5104840695858002),
 (21, 0.5175435394048691),
 (22, 0.5148294270038605),
 (23, 0.5030351877212524),
 (24, 0.47822360694408417),
 (25, 0.4957292526960373),
 (26, 0.4793712943792343),
 (27, 0.4962321072816849),
 (28, 0.5001604110002518),
 (29, 0.5330627411603928),
 (30, 0.5132348090410233),
 (31, 0.5304568558931351),
 (32, 0.5359468162059784),
 (33, 0.5364599078893661),
 (34, 0.5494490414857864),
 (35, 0.5256750583648682),
 (36, 0.5147978961467743),
 (37, 0.5237527340650558),
 (38, 0.5251158028841019),
 (39, 0.5073458850383759),
 (40, 0.503828302025795),
 (41, 0.505394235253334),
 (

In [44]:
dfGradeVCruzada = pd.DataFrame({"AUC":[g[1] for g in gradeVCruzada['resultados']],
                                "Rodadas":[g[0] for g in gradeVCruzada['resultados']]})

In [45]:
fig = linhaAUC(dfGradeVCruzada, fig=fig, legend="Validação Cruzada")

In [46]:
plataforma = os.name
arquivoSaida = os.path.join('imagens', 'xgBoost_AUC_{rotulo}_{plataforma}.png'.format(rotulo=resultado,
                                                                                      plataforma=plataforma))
fig.toolbar_location = None
fig.toolbar.logo = None
export_png(fig, filename=arquivoSaida)

'/media/stelling/OS/xampp/htdocs/KDD2009/python/imagens/xgBoost_AUC_upselling_posix.png'

[](file:///media/stelling/OS/xampp/htdocs/KDD2009/python/imagens/xgBoost_AUC_churn.png')

# AUC/Rodada

#### Ubuntu
![nada](imagens/xgBoost_AUC_upselling_posix.png)

# Conclusão
**TODO**
